 <a name="1"></a>
# <span style="color:green">Задачи исследования:<span>

Исследовать архив объявлений о продаже квартир в Санкт-Петербурге и соседних населённых пунктов за несколько лет и определить рыночную стоимость объектов недвижимости.

По каждой квартире на продажу доступны два вида данных:
* первые вписаны пользователем
* вторые — получены автоматически на основе картографических данных. Например, расстояние до центра, аэропорта, ближайшего парка и водоёма.

# План 

## 1. Осмотр и изучение данных

## 2. Предобработка данных

- проверка и предварительный анализ
- подготовка и очистка (каждую колонку)

## 3. Добавление данных
- добавление дополнительных метрик

## 4. Исследовательский анализ данных


## 5. Выводы и результаты исследования

* Изучите следующие параметры: площадь, цена, число комнат, высота потолков.
  Постройте гистограммы для каждого параметра.

* Изучите время продажи квартиры. Постройте гистограмму. Посчитайте среднее и медиану.
  Опишите, сколько обычно занимает продажа. Когда можно считать, что продажи прошли очень быстро, а когда необычно долго?

* Уберите редкие и выбивающиеся значения. Опишите, какие особенности обнаружили.

* Какие факторы больше всего влияют на стоимость квартиры?
  Изучите, зависит ли цена от квадратного метра, числа комнат, этажа (первого или последнего), удалённости от центра.
  Также изучите зависимость от даты размещения: дня недели, месяца и года.

* Выберите 10 населённых пунктов с наибольшим числом объявлений.
  Посчитайте среднюю цену квадратного метра в этих населённых пунктах.
  Выделите населённые пункты с самой высокой и низкой стоимостью жилья.
  Эти данные можно найти по имени в столбце `locality_name`.

* Изучите предложения квартир: для каждой квартиры есть информация о расстоянии до центра.
  Выделите квартиры в Санкт-Петербурге (`locality_name`). Ваша задача — выяснить, какая область входит в центр.
  Создайте столбец с расстоянием до центра в километрах: округлите до целых значений.
  После этого посчитайте среднюю цену для каждого километра.
  Постройте график: он должен показывать, как цена зависит от удалённости от центра.
  Определите границу, где график сильно меняется — это и будет центральная зона.

* Выделите сегмент квартир в центре.
  Проанализируйте эту территорию и изучите следующие параметры: площадь, цена, число комнат, высота потолков.
  Также выделите факторы, которые влияют на стоимость квартиры (число комнат, этаж, удалённость от центра, дата размещения объявления). Сделайте выводы. Отличаются ли они от общих выводов по всему городу?

# 1. Импорт библиотек и чтение данных

In [1]:
import random
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
pd.set_option('display.max_columns', None)

In [3]:
df = pd.read_csv('datasets/eda_real_estate_data.csv', sep='\t')

In [4]:
df.head()

building_series_id  total_images  last_price  total_area  \
0            1564812            20  13000000.0       108.0   
1                NaN             7   3350000.0        40.4   
2         Сталинский            10   5196000.0        56.0   
3                NaN             0  64900000.0       159.0   
4                NaN             2  10000000.0       100.0   

  first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
0  2019-03-07T00:00:00      3            2.70          16.0         51.0   
1  2018-12-04T00:00:00      1             NaN          11.0         18.6   
2  2015-08-20T00:00:00      2             NaN           5.0         34.3   
3  2015-07-24T00:00:00      3             NaN          14.0          NaN   
4  2018-06-19T00:00:00      2            3.03          14.0         32.0   

   floor is_apartment  studio   area  open_plan  kitchen_area  balcony  \
0      8          NaN   False  108.0      False          25.0      NaN   
1      1          NaN   False   40.4      False          11.0      2.0   
2      4          NaN   False   56.0      False           8.3      0.0   
3      9          NaN   False  159.0      False           NaN      0.0   
4     13          NaN   False  100.0      False          41.0      NaN   

     locality_name  airports_nearest  cityCenters_nearest  parks_around3000  \
0  Санкт-Петербург           18863.0              16028.0               1.0   
1   посёлок Шушары           12817.0              18603.0               0.0   
2  Санкт-Петербург           21741.0              13933.0               1.0   
3  Санкт-Петербург           28098.0               6800.0               2.0   
4  Санкт-Петербург           31856.0               8098.0               2.0   

   parks_nearest  ponds_around3000  ponds_nearest  days_exposition  
0          482.0               2.0          755.0              NaN  
1            NaN               0.0            NaN             81.0  
2           90.0               2.0          574.0            558.0  
3           84.0               3.0          234.0            424.0  
4          112.0               1.0           48.0            121.0

In [5]:
df.sample(5)

building_series_id  total_images  last_price  total_area  \
23241            1564801            10   4390000.0        44.0   
23107                NaN            19   3690000.0        39.2   
17069                NaN            11   8000000.0       100.0   
17992          1564812.0            15  14990000.0       123.0   
11781                NaN             8   5100000.0        60.0   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
23241  2019-01-22T00:00:00      2            2.55           9.0         27.4   
23107  2018-05-18T00:00:00      1             NaN          22.0         16.5   
17069  2017-12-18T00:00:00      5            2.70          25.0          NaN   
17992  2016-09-06T00:00:00      3            3.10          12.0         62.0   
11781  2015-01-20T00:00:00      2             NaN           9.0         31.0   

       floor is_apartment  studio   area  open_plan  kitchen_area  balcony  \
23241      8          NaN   False   44.0      False           6.7      NaN   
23107      2        False   False   39.2      False           9.6      2.0   
17069     10          NaN   False  100.0      False           NaN      NaN   
17992     12          NaN   False  123.0      False          28.0      NaN   
11781      6          NaN   False   60.0      False           9.0      2.0   

         locality_name  airports_nearest  cityCenters_nearest  \
23241  Санкт-Петербург           29476.0              12337.0   
23107   посёлок Мурино               NaN                  NaN   
17069  Санкт-Петербург           16248.0              13838.0   
17992       Сестрорецк           57575.0              34505.0   
11781  Санкт-Петербург           40880.0              16747.0   

       parks_around3000  parks_nearest  ponds_around3000  ponds_nearest  \
23241               0.0            NaN               1.0          441.0   
23107               NaN            NaN               NaN            NaN   
17069               0.0            NaN               2.0          162.0   
17992               2.0          428.0               1.0          615.0   
11781               0.0            NaN               0.0            NaN   

       days_exposition  
23241             80.0  
23107             55.0  
17069             60.0  
17992            656.0  
11781            743.0

In [6]:
# по желанию можно поменять местами значения стобцов для удобства работы командой 
# df[[name_column_1, name_column2, . . . name_column_n]]

### Описание данных
* airports_nearest — расстояние до ближайшего аэропорта в метрах (м)
* balcony — число балконов
* ceiling_height — высота потолков (м)
* cityCenters_nearest — расстояние до центра города (м)
* days_exposition — сколько дней было размещено объявление (от публикации до снятия)
* first_day_exposition — дата публикации
* floor — этаж
* floors_total — всего этажей в доме
* is_apartment — апартаменты (булев тип)
* kitchen_area — площадь кухни (м²)
* last_price — цена на момент снятия с публикации
* living_area — жилая площадь (м²)
* locality_name — название населённого пункта
* open_plan — свободная планировка (булев тип)
* parks_around3000 — число парков в радиусе 3 км
* parks_nearest — расстояние до ближайшего парка (м)
* ponds_around3000 — число водоёмов в радиусе 3 км
* ponds_nearest — расстояние до ближайшего водоёма (м)
* rooms — число комнат
* studio — квартира-студия (булев тип)
* total_area — площадь квартиры в квадратных метрах (м²)
* total_images — число фотографий квартиры в объявлении

# 2. Проверка данных и предварительный анализ

In [7]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 23699 entries, 0 to 23698
Data columns (total 24 columns):
building_series_id      6517 non-null object
total_images            23699 non-null int64
last_price              23699 non-null float64
total_area              23699 non-null float64
first_day_exposition    23699 non-null object
rooms                   23699 non-null int64
ceiling_height          14504 non-null float64
floors_total            23613 non-null float64
living_area             21796 non-null float64
floor                   23699 non-null int64
is_apartment            2775 non-null object
studio                  23699 non-null bool
area                    23699 non-null float64
open_plan               23699 non-null bool
kitchen_area            21421 non-null float64
balcony                 12180 non-null float64
locality_name           23650 non-null object
airports_nearest        18157 non-null float64
cityCenters_nearest     18180 non-null float64
parks_around3000

In [8]:
df.describe()

total_images    last_price    total_area         rooms  ceiling_height  \
count  23699.000000  2.369900e+04  23699.000000  23699.000000    14504.000000   
mean       9.858475  6.541549e+06     60.348651      2.070636        2.771499   
std        5.682529  1.088701e+07     35.654083      1.078405        1.261056   
min        0.000000  1.219000e+04     12.000000      0.000000        1.000000   
25%        6.000000  3.400000e+06     40.000000      1.000000        2.520000   
50%        9.000000  4.650000e+06     52.000000      2.000000        2.650000   
75%       14.000000  6.800000e+06     69.900000      3.000000        2.800000   
max       50.000000  7.630000e+08    900.000000     19.000000      100.000000   

       floors_total   living_area         floor          area  kitchen_area  \
count  23613.000000  21796.000000  23699.000000  23699.000000  21421.000000   
mean      10.673824     34.457852      5.892358     60.348651     10.569807   
std        6.597173     22.030445      4.885249     35.654083      5.905438   
min        1.000000      2.000000      1.000000     12.000000      1.300000   
25%        5.000000     18.600000      2.000000     40.000000      7.000000   
50%        9.000000     30.000000      4.000000     52.000000      9.100000   
75%       16.000000     42.300000      8.000000     69.900000     12.000000   
max       60.000000    409.700000     33.000000    900.000000    112.000000   

            balcony  airports_nearest  cityCenters_nearest  parks_around3000  \
count  12180.000000      18157.000000         18180.000000      18181.000000   
mean       1.150082      28793.672193         14191.277833          0.611408   
std        1.071300      12630.880622          8608.386210          0.802074   
min        0.000000          0.000000           181.000000          0.000000   
25%        0.000000      18585.000000          9238.000000          0.000000   
50%        1.000000      26726.000000         13098.500000          0.000000   
75%        2.000000      37273.000000         16293.000000          1.000000   
max        5.000000      84869.000000         65968.000000          3.000000   

       parks_nearest  ponds_around3000  ponds_nearest  days_exposition  
count    8079.000000      18181.000000    9110.000000     20518.000000  
mean      490.804555          0.770255     517.980900       180.888634  
std       342.317995          0.938346     277.720643       219.727988  
min         1.000000          0.000000      13.000000         1.000000  
25%       288.000000          0.000000     294.000000        45.000000  
50%       455.000000          1.000000     502.000000        95.000000  
75%       612.000000          1.000000     729.000000       232.000000  
max      3190.000000          3.000000    1344.000000      1580.000000

In [9]:
df.head()

building_series_id  total_images  last_price  total_area  \
0            1564812            20  13000000.0       108.0   
1                NaN             7   3350000.0        40.4   
2         Сталинский            10   5196000.0        56.0   
3                NaN             0  64900000.0       159.0   
4                NaN             2  10000000.0       100.0   

  first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
0  2019-03-07T00:00:00      3            2.70          16.0         51.0   
1  2018-12-04T00:00:00      1             NaN          11.0         18.6   
2  2015-08-20T00:00:00      2             NaN           5.0         34.3   
3  2015-07-24T00:00:00      3             NaN          14.0          NaN   
4  2018-06-19T00:00:00      2            3.03          14.0         32.0   

   floor is_apartment  studio   area  open_plan  kitchen_area  balcony  \
0      8          NaN   False  108.0      False          25.0      NaN   
1      1          NaN   False   40.4      False          11.0      2.0   
2      4          NaN   False   56.0      False           8.3      0.0   
3      9          NaN   False  159.0      False           NaN      0.0   
4     13          NaN   False  100.0      False          41.0      NaN   

     locality_name  airports_nearest  cityCenters_nearest  parks_around3000  \
0  Санкт-Петербург           18863.0              16028.0               1.0   
1   посёлок Шушары           12817.0              18603.0               0.0   
2  Санкт-Петербург           21741.0              13933.0               1.0   
3  Санкт-Петербург           28098.0               6800.0               2.0   
4  Санкт-Петербург           31856.0               8098.0               2.0   

   parks_nearest  ponds_around3000  ponds_nearest  days_exposition  
0          482.0               2.0          755.0              NaN  
1            NaN               0.0            NaN             81.0  
2           90.0               2.0          574.0            558.0  
3           84.0               3.0          234.0            424.0  
4          112.0               1.0           48.0            121.0

In [10]:
df.duplicated().sum()

0

In [11]:
# Проверим столбцы которые могут быть схожи
df[df['area'] != df['total_area']]

Empty DataFrame
Columns: [building_series_id, total_images, last_price, total_area, first_day_exposition, rooms, ceiling_height, floors_total, living_area, floor, is_apartment, studio, area, open_plan, kitchen_area, balcony, locality_name, airports_nearest, cityCenters_nearest, parks_around3000, parks_nearest, ponds_around3000, ponds_nearest, days_exposition]
Index: []

### Выводы по предварительному анализу

- Неизвестное значение столбцов building_series_id и is_apartment    
- Пропуски значений в стобцах:
    - building_series_id    
    - ceiling_height 
    - living_area
    - floors_total
    - is_apartment 
    - kitchen_area
    - balcony  
    - locality_name 
    - airports_nearest 
    - cityCenters_nearest
    - parks_around3000    
    - parks_nearest  
    - ponds_around3000 
    - days_exposition  
- Столбец rooms c минимальным занчение 0 - выглядит странно
- Повтор столбцов total_area и area
- Столбец first_day_exposition тип не datetime
- Столбец ceiling_height слишком высоко макс занчение высоты потолков
- Стобец floors_total тоже слишком велик с макс значением если это не БЦ "Лахта Центр"
- Столбец kitchen_area слишком экстремально минимальное значение.


**В датасете** имеются пропуски и экстремально критические значение в столбцах, которые бросились в глаза при первичном осмотре, также встретилось дублирование столбцов, о котором следует учесть при дальнейших выгрузках.

# 3. Подготовка и очистка данных

## 3.1. Индексы и названия столбцов

In [12]:
# 1 столбец выбивается из списка CamelCase исправим
df.rename(columns={'cityCenters_nearest': 'city_centers_nearest'}, inplace=True)
# Проверим
df.columns.tolist()

['building_series_id',
 'total_images',
 'last_price',
 'total_area',
 'first_day_exposition',
 'rooms',
 'ceiling_height',
 'floors_total',
 'living_area',
 'floor',
 'is_apartment',
 'studio',
 'area',
 'open_plan',
 'kitchen_area',
 'balcony',
 'locality_name',
 'airports_nearest',
 'city_centers_nearest',
 'parks_around3000',
 'parks_nearest',
 'ponds_around3000',
 'ponds_nearest',
 'days_exposition']

## 3.2. Работа с дубликатами

In [13]:
# Удаляем дубликаты столбцов
df.drop(['area'], axis=1, inplace=True)


In [14]:
# Проверяем 
df.head(0)

Empty DataFrame
Columns: [building_series_id, total_images, last_price, total_area, first_day_exposition, rooms, ceiling_height, floors_total, living_area, floor, is_apartment, studio, open_plan, kitchen_area, balcony, locality_name, airports_nearest, city_centers_nearest, parks_around3000, parks_nearest, ponds_around3000, ponds_nearest, days_exposition]
Index: []

## 3.3. Поиск пропущенных значений

- building_series_id    
- ceiling_height 
- living_area
- floors_total
- is_apartment 
- kitchen_area
- balcony  
- locality_name 
- airports_nearest 
- cityCenters_nearest
- parks_around3000    
- parks_nearest  
- ponds_around3000 
- days_exposition 

In [15]:
# Смотрим что с пропущенными значениями в процентном отношении
null_percentage = df.isnull().sum().sort_values(ascending=False)/len(df)*100
null_quantity = df.isnull().sum().sort_values(ascending=False)
col_isnull = pd.concat([null_percentage, null_quantity], axis=1)
col_isnull.columns = ['null_percentage','null_quantity']
col_isnull

null_percentage  null_quantity
is_apartment                88.290645          20924
building_series_id          72.500949          17182
parks_nearest               65.909954          15620
ponds_nearest               61.559559          14589
balcony                     48.605426          11519
ceiling_height              38.799105           9195
airports_nearest            23.384953           5542
city_centers_nearest        23.287902           5519
ponds_around3000            23.283683           5518
parks_around3000            23.283683           5518
days_exposition             13.422507           3181
kitchen_area                 9.612220           2278
living_area                  8.029875           1903
floors_total                 0.362885             86
locality_name                0.206760             49
open_plan                    0.000000              0
floor                        0.000000              0
rooms                        0.000000              0
first_day_exposition         0.000000              0
total_area                   0.000000              0
last_price                   0.000000              0
total_images                 0.000000              0
studio                       0.000000              0

### 3.3.1 Изучение пропусков

Изучение пропусков стоит начинать с самых важных на первый взгляд показателей. Так как это не заставит сначала решать задачи по замене пропусков неважных признаков. Они и воовсе могут удалиться как дубликаты или удалиться совсем из за отстутсвия нескольких важных признаков.

### Местоположение

- locality_name

Один из важнейших параметров выборки. Не зная местоположения, врядли кто то будет покупать квартиру. Так как данных столбцов всего 49, то из можно удалить.

In [16]:
# Удаляем и проверяем
df.dropna(subset=['locality_name'], inplace=True)

df['locality_name'].isna().sum()

0

In [17]:
# Чтобы узнать есть ли повторяющиеся значения проведем несколько операций
# df['locality_name'] = df['locality_name'].str.lower() # не принесло успеха но читаемость хуже
df['locality_name'].unique().tolist()

['Санкт-Петербург',
 'посёлок Шушары',
 'городской посёлок Янино-1',
 'посёлок Парголово',
 'посёлок Мурино',
 'Ломоносов',
 'Сертолово',
 'Петергоф',
 'Пушкин',
 'деревня Кудрово',
 'Коммунар',
 'Колпино',
 'поселок городского типа Красный Бор',
 'Гатчина',
 'поселок Мурино',
 'деревня Фёдоровское',
 'Выборг',
 'Кронштадт',
 'Кировск',
 'деревня Новое Девяткино',
 'посёлок Металлострой',
 'посёлок городского типа Лебяжье',
 'посёлок городского типа Сиверский',
 'поселок Молодцово',
 'поселок городского типа Кузьмоловский',
 'садовое товарищество Новая Ропша',
 'Павловск',
 'деревня Пикколово',
 'Всеволожск',
 'Волхов',
 'Кингисепп',
 'Приозерск',
 'Сестрорецк',
 'деревня Куттузи',
 'посёлок Аннино',
 'поселок городского типа Ефимовский',
 'посёлок Плодовое',
 'деревня Заклинье',
 'поселок Торковичи',
 'поселок Первомайское',
 'Красное Село',
 'посёлок Понтонный',
 'Сясьстрой',
 'деревня Старая',
 'деревня Лесколово',
 'посёлок Новый Свет',
 'Сланцы',
 'село Путилово',
 'Ивангород',
 '

Посмотрим на значения населенных пунктов построчно их не так много
После просмотра видим
- 'посёлок мурино'
- 'поселок мурино'

Производим замену 

In [18]:
df['locality_name'] = df['locality_name'].str.replace('ё', 'е', regex=True)

In [19]:
len(df['locality_name'].unique())

330

In [20]:
# Топ 10
df['locality_name'].value_counts()[:10]

Санкт-Петербург      15721
поселок Мурино         556
поселок Шушары         440
Всеволожск             398
Пушкин                 369
Колпино                338
поселок Парголово      327
Гатчина                307
деревня Кудрово        299
Выборг                 237
Name: locality_name, dtype: int64

### Апартаменты

In [21]:
# Пока до конца не ясно что это за признак, 
# скореее всего это жилой или не жилой фонд
df['is_apartment'].value_counts()

False    2710
True       50
Name: is_apartment, dtype: int64

In [22]:
df['is_apartment'].unique()

array([nan, False, True], dtype=object)

In [23]:
# Меняем на жилой фонд
df['is_apartment'] = df['is_apartment'].fillna(False)
# Проверка
df['is_apartment'].isna().sum()

0

**Данный** признак не понадобиться для дальнейшего анализа, по этому проблемы с пропусками решаем не задумываясь заменой на False - (значит жилой фонд) к тому же анализ проводиться не по комерческой недвижимости.

### Тип строения

In [24]:
df['building_series_id'].unique()

array(['1564812', nan, 'Сталинский', '1568627.0', '1564812.0',
       '1568643.0', '1564806.0', '1564796.0', '1569038.0', '1564801.0',
       '1564801', '1569071.0', '1564792', 'Панельный', '1569071',
       '1564792.0', '1569054.0', '1569033.0', '504', '1569066',
       '600.11 серия', '1568690.0', '1564806', '712041.0', 'Брежневка',
       '1568627', '1568663.0', 'Старый фонд с КР', '1568734.0',
       '137 серия', 'сталинский', '712041', '1569066.0', 'Хрущевка',
       '600', '1569033', '1568675.0', 'Кирпичный монолит', '1564796',
       'Индивидуальный', 'старый фонд', 'кирп.монолит', 'Кирпичный',
       '1568663', 'Старый фонд', '1568658', 'Кирп.Монолит', '1569075.0',
       '1568658.0', '7', '1569038', '1569054', '1569061.0',
       '121 (Гатчинская)', '1568675', '602 серия', '1 ЛГ - 600.11', '137',
       '606 серия', '1569088.0', '1569048.0', '100', '1568643',
       '1569041.0', '121', '1569079.0', '1569041', 'хрущевка', 'Блочный',
       'старый фонд + капремонт', 'монолит', 

**Похоже** что стобец ```building_series_id``` характеризует конструктивное решения здания, которое не потребуется в исследовании

### Вид данных полученный автоматически. 

- parks_nearest
- ponds_nearest
- ponds_around3000
- parks_around3000
- city_centers_nearest
- airports_nearest

В данных которые получены автоматически пропуски убирать не будем

### Балконы
- balcony

In [25]:
# Количество пропусков
df['balcony'].isna().sum()

11513

In [26]:
# Взглянем на общее распределение + 11519 пропущенных значений
df['balcony'].value_counts()

1.0    4187
0.0    3725
2.0    3658
5.0     304
4.0     182
3.0      81
Name: balcony, dtype: int64

In [27]:
# Посмотрим какое количество отсутствующих значений в столбце балконы на 1 этаже здания
df[(df['balcony'].isna()) & (df['floor'] == 1)]

building_series_id  total_images  last_price  total_area  \
16                   NaN            11   6700000.0        82.0   
37                   NaN            10   1990000.0        45.8   
70                   NaN             9   3400000.0        30.0   
76                   NaN            12   2800000.0        55.1   
84             1564812.0            11   2400000.0        43.9   
...                  ...           ...         ...         ...   
23651                NaN             7   3350000.0        41.0   
23663                NaN            12   6400000.0        88.0   
23680          1569088.0            14   5000000.0        59.0   
23696                NaN            18   2500000.0        56.7   
23698                NaN             4   1350000.0        32.3   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
16     2017-11-23T00:00:00      3            3.05           5.0        55.60   
37     2017-10-28T00:00:00      2            2.50           5.0          NaN   
70     2018-09-05T00:00:00      1             NaN           5.0        16.00   
76     2016-05-14T00:00:00      3            2.60           5.0        38.40   
84     2019-03-13T00:00:00      2             NaN           2.0        27.46   
...                    ...    ...             ...           ...          ...   
23651  2018-12-17T00:00:00      1             NaN           6.0        18.00   
23663  2018-01-12T00:00:00      4            2.55          10.0          NaN   
23680  2019-04-04T00:00:00      3            2.50           5.0        52.00   
23696  2018-02-11T00:00:00      2             NaN           3.0        29.70   
23698  2017-07-21T00:00:00      1            2.50           5.0        12.30   

       floor  is_apartment  studio  open_plan  kitchen_area  balcony  \
16         1         False   False      False           9.0      NaN   
37         1         False   False      False           NaN      NaN   
70         1         False   False      False           7.0      NaN   
76         1         False   False      False           4.9      NaN   
84         1         False   False      False           5.2      NaN   
...      ...           ...     ...        ...           ...      ...   
23651      1         False   False      False          12.0      NaN   
23663      1         False   False      False           NaN      NaN   
23680      1         False   False      False           7.0      NaN   
23696      1         False   False      False           NaN      NaN   
23698      1         False   False      False           9.0      NaN   

                             locality_name  airports_nearest  \
16                         Санкт-Петербург           22108.0   
37     поселок городского типа Красный Бор               NaN   
70                         Санкт-Петербург           39053.0   
76                                 Кировск               NaN   
84                                 Кировск               NaN   
...                                    ...               ...   
23651      поселок городского типа Токсово               NaN   
23663                      Санкт-Петербург           33642.0   
23680                      Санкт-Петербург           26835.0   
23696                     село Рождествено               NaN   
23698                  поселок Новый Учхоз               NaN   

       city_centers_nearest  parks_around3000  parks_nearest  \
16                  10698.0               3.0          420.0   
37                      NaN               NaN            NaN   
70                   8313.0               1.0          382.0   
76                      NaN               NaN            NaN   
84                      NaN               NaN            NaN   
...                     ...               ...            ...   
23651                   NaN               NaN            NaN   
23663               13943.0               0.0            NaN   
23680               11878.0               

In [28]:
# Меняем значение Nan на 0
df['balcony'] = df['balcony'].fillna(0)
# Проверяем замену
df['balcony'].isnull().sum()

0

In [29]:
# Меняем тип данных с float64 на int 
df['balcony'] = df['balcony'].astype(int)

In [30]:
df['balcony'].value_counts()

0    15238
1     4187
2     3658
5      304
4      182
3       81
Name: balcony, dtype: int64

**Если** человек не указал количество балконов -  это скорее всего означает что их нет, так как вероятность того что их нет выше чем вероятность того что он забыл их указать. Наличие балкона это несравненный плюс нежели его отсутствие. Также можно предположить что в частных строениях, часто будет отсутствовать данный признак.
Поэтому произвели замену на 0 и данный признак привели к целочисленному типу данных

### Высота потолков
- ceiling_height	

In [31]:
# Напомним количество пропущенных значений
df['ceiling_height'].isna().value_counts()

False    14490
True      9160
Name: ceiling_height, dtype: int64

In [32]:
# Посмотрим на параметры высоты потолков
df['ceiling_height'].describe()

count    14490.000000
mean         2.771287
std          1.261593
min          1.000000
25%          2.520000
50%          2.650000
75%          2.800000
max        100.000000
Name: ceiling_height, dtype: float64

Посмотрим на выборку с разными срезами, присутствуют как предельно низкие, так и слишком высокие значения.

In [33]:
# Высота потолков меньше 2 метров
len(df[df['ceiling_height'] <= 2])

14

In [34]:
# Высота которая меньше ГОСТ жилых зданий
len(df[df['ceiling_height'] <= 2.4])

44

In [35]:
# Высота больше 6 метров
len(df[df['ceiling_height'] > 5])

36

In [36]:
df['ceiling_height'] = df['ceiling_height'].fillna(2.5) 
# Проверим замену

df['ceiling_height'].isna().sum()

0

**Вывод:**

Важность данного параметра не высока.

Исследовав высоту потолков можно отметить что в выборке присутствуют выбросы. Так как трудно представить, метровый потолок в многоэтажном здании также как и более 5 метров. Здесь пропуски логично заменить на минимальное значение ГОСТ для зданий и сообружений - 2,5 метра. 

### Количество дней размещения публикации
- days_exposition

Данный параметр может показать ликвидность обьекта от места расположения и привлекательность района.
Пока оставим отсутствующие значения без изменений.

In [37]:
# Попробуем сделать из значения "days_exposition" что то вроде параметра ликвидности 

def category_days_exposition(days):
    """
    ВАЖНО! данный параметр всегда сравнивается с показателем средней цены по району
    в вакуме не рассматривается
    
    Параметры могут изменяться в зависимости от географич. расположения и  экономической ситиации
    
    Разбиваем на категории ликвидности:
    1 - высокая ликвидность
    2, 3 - нормальная ликвидность
    4 - низкая ликвидность
    5 - отсутствие ликвидности (повторюсь что на эту метрику влияют другие параметры)
    """
    if days < 50:
        return 1
    elif days < 100:
        return 2
    elif days < 200:
        return 3
    elif days < 350:
        return 4
    else:
        return 5
    


In [38]:
df['category_days_exposition'] = df['days_exposition'].apply(category_days_exposition)

In [39]:
# Учитываем что в 5 категории присутствуют отсутствующие значеия
df['category_days_exposition'].value_counts()

5    6419
1    6281
2    4209
3    4114
4    2627
Name: category_days_exposition, dtype: int64

In [40]:
df['days_exposition'] = df['days_exposition'].fillna(df['days_exposition'].median())

In [41]:
df['days_exposition'].isna().sum()

0

**Вывод:**

Исследовав количество дней размещения публикации, разбили данный признак на категории чтобы посмотреть на общую картину. Здесь возможно поиграться с созданной категорией увеличив или уменьшив сроки для создания категорий. Важно заметить что разделение на категории должен работать совместно с другими показателями, например такие как цена и район

По вопросу отсутствия данного значения нужно разговаривать с разработчиками или администратором баз данных. Информация о размещении и дне снятия с публикации должна присутствовать в системе.
При вынужденной замене лучше выбрать медианное значение.

### Жилая площадь
- living_area

Стоит заметить что здесь очень важно понимать разницу (как толкует ее Жилищный Кодекс) между 
- **жилой площадью** - сумма площадей жилых комнат. Кухня, ванна, туалет, балкон и подобные им комнаты не являются частью жилой площади
- **общей площадью** – сумма площадей всех комнат, составляющих данную квартиру, в том числе подсобных помещений, кроме лоджий, балконов, веранд и террас. К подсобным помещениям относятся площади кухонь, коридоров, ванных, санузлов, встроенных шкафов, кладовых, а также площадь, занятая внутриквартирной лестницей.

### Площадь кухни
- kitchen_area


In [42]:
# Посмотрим сколько значений отсуттвует в квартирах студиях, так как она совмещена с другой комнатой
df[(df['kitchen_area'].isna()) & (df['studio'] == True)]

building_series_id  total_images  last_price  total_area  \
144                  NaN             1   2450000.0       27.00   
440                  NaN             8   2480000.0       27.11   
608                  NaN             2   1850000.0       25.00   
697                  NaN            12   2500000.0       24.10   
716                  NaN             5   1500000.0       17.00   
...                  ...           ...         ...         ...   
22867                NaN             8   3090000.0       30.00   
22877                NaN             2   4280000.0       28.00   
23210                NaN             7   3200000.0       26.00   
23554                NaN            15   3350000.0       26.00   
23637                NaN             8   2350000.0       26.00   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
144    2017-03-30T00:00:00      0            2.50          24.0        15.50   
440    2018-03-12T00:00:00      0            2.50          17.0        24.75   
608    2019-02-20T00:00:00      0            2.50          10.0          NaN   
697    2017-12-01T00:00:00      0            2.75          25.0        17.50   
716    2017-06-07T00:00:00      0            2.70           9.0        12.00   
...                    ...    ...             ...           ...          ...   
22867  2017-12-17T00:00:00      0            2.50          25.0        18.20   
22877  2017-10-26T00:00:00      0            2.70          19.0        18.00   
23210  2017-09-01T00:00:00      0            2.50          25.0        18.00   
23554  2018-09-07T00:00:00      0            2.50          19.0          NaN   
23637  2018-06-26T00:00:00      0            2.50          25.0        17.00   

       floor  is_apartment  studio  open_plan  kitchen_area  balcony  \
144        2         False    True      False           NaN        2   
440        4         False    True      False           NaN        2   
608        7         False    True      False           NaN        0   
697       21         False    True      False           NaN        0   
716        1         False    True      False           NaN        0   
...      ...           ...     ...        ...           ...      ...   
22867      5         False    True      False           NaN        0   
22877     10         False    True      False           NaN        0   
23210     16         False    True      False           NaN        0   
23554      8         False    True      False           NaN        0   
23637      4         False    True      False           NaN        2   

         locality_name  airports_nearest  city_centers_nearest  \
144     поселок Мурино               NaN                   NaN   
440    Санкт-Петербург           38171.0               15015.0   
608     поселок Шушары               NaN                   NaN   
697    деревня Кудрово               NaN                   NaN   
716     поселок Шушары           18654.0               29846.0   
...                ...               ...                   ...   
22867  Санкт-Петербург           35250.0               16414.0   
22877  Санкт-Петербург           18982.0                7206.0   
23210  Санкт-Петербург           11405.0               13222.0   
23554  Санкт-Петербург           18090.0               17092.0   
23637    поселок Бугры               NaN                   NaN   

       parks_around3000  parks_nearest  ponds_around3000  ponds_nearest  \
144                 NaN            NaN               NaN            NaN   
440                 0.0            NaN               2.0          982.0   
608                 NaN            NaN               NaN            NaN   
697                 NaN            NaN               NaN            NaN   
716                 0.0            NaN               0.0            NaN   
...                 ...            ...               ...            ...   
22867               0.0            NaN               1.0          400

Менять отсутствующие значения столбца ```kitchen_area``` на среднюю или медиану не целесообразно так как общая площадь квартир совершенно разная. 

#### Поэтому:

- Здесь мы должны либо выделить категории в зависимости от общей площади, далее в каждой категории посмотреть среднюю или медиану площади кухни и уже заполнять значения.
- Либо категоризировать по количеству комнат и уже заполнять значения в зависимости от среднего или медианы этого параметра.

В любом случае если производить замену нужно категоризировать квартиры по какому либо признаку.

### Этажность дома  
- floors_total

In [43]:
df['floors_total'].isna().sum()

85

В дальнейшем этот показатель поможет нам категоризировать недвижимость с последним этажом.
Пропуски не критичны, но мы поступим следующим образом. 
- 🚫 - Из всей выборки возьмем процент последнего этажа и заполним хотя бы часть этих значений, 
- ✔️ - Заполним значения цифрой 1 так как это могут быть частные дома

In [44]:
df['floors_total'] = df['floors_total'].fillna(1)
# Проверяем пропуски
df['floors_total'].isna().sum()

0

In [45]:
df.head()

building_series_id  total_images  last_price  total_area  \
0            1564812            20  13000000.0       108.0   
1                NaN             7   3350000.0        40.4   
2         Сталинский            10   5196000.0        56.0   
3                NaN             0  64900000.0       159.0   
4                NaN             2  10000000.0       100.0   

  first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
0  2019-03-07T00:00:00      3            2.70          16.0         51.0   
1  2018-12-04T00:00:00      1            2.50          11.0         18.6   
2  2015-08-20T00:00:00      2            2.50           5.0         34.3   
3  2015-07-24T00:00:00      3            2.50          14.0          NaN   
4  2018-06-19T00:00:00      2            3.03          14.0         32.0   

   floor  is_apartment  studio  open_plan  kitchen_area  balcony  \
0      8         False   False      False          25.0        0   
1      1         False   False      False          11.0        2   
2      4         False   False      False           8.3        0   
3      9         False   False      False           NaN        0   
4     13         False   False      False          41.0        0   

     locality_name  airports_nearest  city_centers_nearest  parks_around3000  \
0  Санкт-Петербург           18863.0               16028.0               1.0   
1   поселок Шушары           12817.0               18603.0               0.0   
2  Санкт-Петербург           21741.0               13933.0               1.0   
3  Санкт-Петербург           28098.0                6800.0               2.0   
4  Санкт-Петербург           31856.0                8098.0               2.0   

   parks_nearest  ponds_around3000  ponds_nearest  days_exposition  \
0          482.0               2.0          755.0             95.0   
1            NaN               0.0            NaN             81.0   
2           90.0               2.0          574.0            558.0   
3           84.0               3.0          234.0            424.0   
4          112.0               1.0           48.0            121.0   

   category_days_exposition  
0                         5  
1                         2  
2                         5  
3                         5  
4                         3

# ДОРАБОТАТЬ

In [46]:
# Находим все квартиры на последнем этаже
df_copy = pd.read_csv('datasets/eda_real_estate_data.csv', sep='\t')
df_copy[(df_copy['floors_total'] == df_copy['floor'])]

building_series_id  total_images  last_price  total_area  \
12                   NaN            10   3890000.0        54.0   
13             1568627.0            20   3550000.0        42.8   
23             1564806.0            11   2950000.0        32.0   
36                   NaN            13   3790000.0        45.0   
43                   NaN            13   9330000.0        48.0   
...                  ...           ...         ...         ...   
23641                NaN             3   3100000.0        30.0   
23644            1564812             7   4990000.0        62.5   
23648          1564812.0            14  10100000.0        78.0   
23660                NaN             1   2950000.0        53.6   
23685          1568627.0            15   2490000.0        31.0   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
12     2016-06-30T00:00:00      2             NaN           5.0         30.0   
13     2017-07-01T00:00:00      2            2.56           5.0         27.0   
23     2016-10-29T00:00:00      1            2.60           9.0         17.7   
36     2017-01-25T00:00:00      2             NaN           9.0         27.0   
43     2017-01-10T00:00:00      2            3.00           4.0         28.0   
...                    ...    ...             ...           ...          ...   
23641  2018-03-28T00:00:00      1            2.50           5.0         17.0   
23644  2018-04-26T00:00:00      2            2.70           4.0         32.3   
23648  2017-05-12T00:00:00      3            3.27           5.0         48.6   
23660  2018-02-01T00:00:00      2            2.75           3.0         32.0   
23685  2019-01-24T00:00:00      1            2.50           5.0         17.3   

       floor is_apartment  studio  area  open_plan  kitchen_area  balcony  \
12         5          NaN   False  54.0      False           9.0      0.0   
13         5          NaN   False  42.8      False           5.2      1.0   
23         9          NaN   False  32.0      False           6.1      NaN   
36         9        False   False  45.0      False           6.3      2.0   
43         4          NaN   False  48.0      False           7.5      NaN   
...      ...          ...     ...   ...        ...           ...      ...   
23641      5          NaN   False  30.0      False           5.0      NaN   
23644      4          NaN   False  62.5      False          12.1      NaN   
23648      5          NaN   False  78.0      False           8.2      NaN   
23660      3        False   False  53.6      False           5.8      1.0   
23685      5          NaN   False  31.0      False           5.6      1.0   

         locality_name  airports_nearest  cityCenters_nearest  \
12           Сертолово               NaN                  NaN   
13            Петергоф           37868.0              33058.0   
23     Санкт-Петербург           15414.0              14211.0   
36     Санкт-Петербург           49574.0              16461.0   
43     Санкт-Петербург           15016.0              10822.0   
...                ...               ...                  ...   
23641          Колпино           24056.0              29843.0   
23644  Санкт-Петербург           20141.0               4415.0   
23648  Санкт-Петербург           20933.0               1113.0   
23660     Красное Село           38293.0              41718.0   
23685        Ломоносов           48393.0              51818.0   

       parks_around3000  parks_nearest  ponds_around3000  ponds_nearest  \
12                  NaN            NaN               NaN            NaN   
13                  1.0          294.0               3.0          298.0   
23                  2.0          517.0               1.0          190.0   
36                  1.0          459.0               0.0            NaN   
43                  0.0            NaN               1.0          492.0   
...                 ...            ...               ...            ...   
23641               0

In [47]:
df_copy['floors_total'].unique()

array([16., 11.,  5., 14., 12., 26., 24., 27.,  9.,  6., 17., 25.,  3.,
       23., 19., 18.,  4., 22.,  8.,  2., 10.,  7., 13., 15., nan, 20.,
       28., 36., 21., 35., 34., 60.,  1., 29., 33., 52., 37.])

In [48]:
# Считаем процент квартир находящхся на последнем этаже
percent = len(df_copy[(df_copy['floors_total'] == df_copy['floor'])])/len(df)*100
percent

14.21141649048626

In [49]:
# Далее берем этот процент от пропусков и считаем сколько пропусков можно заполнить 
85*percent/100

12.07970401691332

In [50]:
df_copy[df_copy['floors_total'].isna()]

building_series_id  total_images  last_price  total_area  \
186                  NaN            12  11640000.0        65.2   
237                  NaN             4   2438033.0        28.1   
457                  NaN             4   9788348.0        70.8   
671                  NaN             4   6051191.0        93.6   
1757                 NaN             5   3600000.0        39.0   
...                  ...           ...         ...         ...   
22542          1564812.0             5   8500000.0        63.5   
22656                NaN             4   4574160.0        64.5   
22808                NaN             0  14569263.0       110.4   
23590                NaN             0  21187872.0       123.3   
23658                NaN             6   3063600.0        43.8   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
186    2018-10-02T00:00:00      2             NaN           NaN        30.80   
237    2016-11-23T00:00:00      1             NaN           NaN        20.75   
457    2015-08-01T00:00:00      2             NaN           NaN        38.40   
671    2017-04-06T00:00:00      3             NaN           NaN        47.10   
1757   2017-04-22T00:00:00      1             NaN           NaN          NaN   
...                    ...    ...             ...           ...          ...   
22542  2017-05-24T00:00:00      2             2.8           NaN          NaN   
22656  2017-04-02T00:00:00      2             NaN           NaN        31.70   
22808  2016-11-20T00:00:00      3             NaN           NaN        45.38   
23590  2017-04-25T00:00:00      3             NaN           NaN        50.40   
23658  2016-11-28T00:00:00      1             2.7           NaN        14.00   

       floor is_apartment  studio   area  open_plan  kitchen_area  balcony  \
186        4          NaN   False   65.2      False         12.00      NaN   
237        1          NaN   False   28.1      False           NaN      0.0   
457       12          NaN   False   70.8      False         10.63      0.0   
671        8          NaN   False   93.6      False         16.80      0.0   
1757       9          NaN   False   39.0      False           NaN      0.0   
...      ...          ...     ...    ...        ...           ...      ...   
22542      3          NaN   False   63.5      False           NaN      NaN   
22656     20          NaN   False   64.5      False         14.40      0.0   
22808      6          NaN   False  110.4      False         23.42      0.0   
23590     18          NaN   False  123.3      False         23.60      0.0   
23658      8          NaN   False   43.8      False         15.50      2.0   

         locality_name  airports_nearest  cityCenters_nearest  \
186    Санкт-Петербург           39197.0              12373.0   
237    Санкт-Петербург           22041.0              17369.0   
457    Санкт-Петербург           37364.0               8322.0   
671    Санкт-Петербург           22041.0              17369.0   
1757   Санкт-Петербург           22735.0              11618.0   
...                ...               ...                  ...   
22542  Санкт-Петербург           51340.0              15363.0   
22656  Санкт-Петербург           22041.0              17369.0   
22808  Санкт-Петербург           19095.0               4529.0   
23590  Санкт-Петербург           19095.0               4529.0   
23658  Санкт-Петербург            8426.0              12082.0   

       parks_around3000  parks_nearest  ponds_around3000  ponds_nearest  \
186                 1.0          123.0               0.0            NaN   
237                 0.0            NaN               1.0          374.0   
457                 2.0          309.0               2.0          706.0   
671                 0.0            NaN               1.0          374.0   
1757                1.0          835.0               1.0          652.0   
...                 ...            ...               ...            ...   
22542    

In [51]:
# Получаем список индексов которые не имеют значения floor_total == nan
row_nan_floor_total = df_copy[df_copy['floors_total'].isna()].index.tolist()

In [52]:
# Получаем 12 рандомных значений строк из списка которые мы будем заменять
random_row_replace = random.choices(row_nan_floor_total, k = 12)
random_row_replace

[22542,
 11129,
 7508,
 23658,
 8478,
 12352,
 10319,
 11389,
 22542,
 23590,
 20146,
 10880]

In [53]:
# встечающаяся этажность квартир где отсутствует общая этажность здания
# берем 12 рандомных значений этажности
floor_random = df_copy[df_copy['floors_total'].isna()]['floor'].unique()
floor_random = random.choices(floor_random, k = 12)
floor_random

[3, 15, 7, 5, 10, 14, 9, 11, 22, 2, 11, 4]

# ДОРАБОТАТЬ

In [54]:
# def replace(df):
#     # получаем строки
#     for i in random_row_replace:
#         # получаем значения для этажей
#         for x in floor_random:
# #             print(x)
#             df.loc[[i]]['floors_total'] = x
#     return df
        

In [55]:
def replac(param):
    # получаем строки
    for i in random_row_replace:
        # получаем значения для этажей
        for x in floor_random:
#             print(x)
            print(df_copy.loc[[i]])
            break
            param.loc[[i]]['floors_total'] = x
    return param

In [56]:
# df_copy['ff'] = df_copy.apply(replac, axis=1)

      building_series_id  total_images  last_price  total_area  \
22542          1564812.0             5   8500000.0        63.5   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
22542  2017-05-24T00:00:00      2             2.8           NaN          NaN   

       floor is_apartment  studio  area  open_plan  kitchen_area  balcony  \
22542      3          NaN   False  63.5      False           NaN      NaN   

         locality_name  airports_nearest  cityCenters_nearest  \
22542  Санкт-Петербург           51340.0              15363.0   

       parks_around3000  parks_nearest  ponds_around3000  ponds_nearest  \
22542               0.0            NaN               1.0          853.0   

       days_exposition  
22542            512.0  
      building_series_id  total_images  last_price  total_area  \
11129                NaN            10   3128418.0       34.53   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
11129 

10319            145.0  
      building_series_id  total_images  last_price  total_area  \
11389                NaN             3   4700000.0        55.2   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
11389  2016-06-23T00:00:00      1             NaN           NaN        18.39   

       floor is_apartment  studio  area  open_plan  kitchen_area  balcony  \
11389      7          NaN   False  55.2      False         15.37      0.0   

         locality_name  airports_nearest  cityCenters_nearest  \
11389  Санкт-Петербург           35234.0              14674.0   

       parks_around3000  parks_nearest  ponds_around3000  ponds_nearest  \
11389               0.0            NaN               1.0          844.0   

       days_exposition  
11389             15.0  
      building_series_id  total_images  last_price  total_area  \
22542          1564812.0             5   8500000.0        63.5   

      first_day_exposition  rooms  ceiling_height  floors_tot

7508             26.0  
      building_series_id  total_images  last_price  total_area  \
23658                NaN             6   3063600.0        43.8   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
23658  2016-11-28T00:00:00      1             2.7           NaN         14.0   

       floor is_apartment  studio  area  open_plan  kitchen_area  balcony  \
23658      8          NaN   False  43.8      False          15.5      2.0   

         locality_name  airports_nearest  cityCenters_nearest  \
23658  Санкт-Петербург            8426.0              12082.0   

       parks_around3000  parks_nearest  ponds_around3000  ponds_nearest  \
23658               2.0           24.0               1.0          271.0   

       days_exposition  
23658            246.0  
     building_series_id  total_images  last_price  total_area  \
8478          1564812.0            19  13500000.0        77.8   

     first_day_exposition  rooms  ceiling_height  floors_total  

20146            183.0  
      building_series_id  total_images  last_price  total_area  \
10880                NaN             5  11990000.0       147.7   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
10880  2017-06-23T00:00:00      5             NaN           NaN          NaN   

       floor is_apartment  studio   area  open_plan  kitchen_area  balcony  \
10880      3          NaN   False  147.7      False           NaN      0.0   

         locality_name  airports_nearest  cityCenters_nearest  \
10880  Санкт-Петербург           20160.0               3252.0   

       parks_around3000  parks_nearest  ponds_around3000  ponds_nearest  \
10880               2.0          320.0               1.0          976.0   

       days_exposition  
10880             88.0  
      building_series_id  total_images  last_price  total_area  \
22542          1564812.0             5   8500000.0        63.5   

      first_day_exposition  rooms  ceiling_height  floors_t

23590            104.0  
      building_series_id  total_images  last_price  total_area  \
20146          1564812.0            16   3850000.0        36.0   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
20146  2018-10-12T00:00:00      1             NaN           NaN         19.0   

       floor is_apartment  studio  area  open_plan  kitchen_area  balcony  \
20146     15          NaN   False  36.0      False           8.5      NaN   

          locality_name  airports_nearest  cityCenters_nearest  \
20146  посёлок Стрельна           28276.0              23454.0   

       parks_around3000  parks_nearest  ponds_around3000  ponds_nearest  \
20146               0.0            NaN               0.0            NaN   

       days_exposition  
20146            183.0  
      building_series_id  total_images  last_price  total_area  \
10880                NaN             5  11990000.0       147.7   

      first_day_exposition  rooms  ceiling_height  floors_t

...

23590            104.0  
      building_series_id  total_images  last_price  total_area  \
20146          1564812.0            16   3850000.0        36.0   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
20146  2018-10-12T00:00:00      1             NaN           NaN         19.0   

       floor is_apartment  studio  area  open_plan  kitchen_area  balcony  \
20146     15          NaN   False  36.0      False           8.5      NaN   

          locality_name  airports_nearest  cityCenters_nearest  \
20146  посёлок Стрельна           28276.0              23454.0   

       parks_around3000  parks_nearest  ponds_around3000  ponds_nearest  \
20146               0.0            NaN               0.0            NaN   

       days_exposition  
20146            183.0  
      building_series_id  total_images  last_price  total_area  \
10880                NaN             5  11990000.0       147.7   

      first_day_exposition  rooms  ceiling_height  floors_t

7508             26.0  
      building_series_id  total_images  last_price  total_area  \
23658                NaN             6   3063600.0        43.8   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
23658  2016-11-28T00:00:00      1             2.7           NaN         14.0   

       floor is_apartment  studio  area  open_plan  kitchen_area  balcony  \
23658      8          NaN   False  43.8      False          15.5      2.0   

         locality_name  airports_nearest  cityCenters_nearest  \
23658  Санкт-Петербург            8426.0              12082.0   

       parks_around3000  parks_nearest  ponds_around3000  ponds_nearest  \
23658               2.0           24.0               1.0          271.0   

       days_exposition  
23658            246.0  
     building_series_id  total_images  last_price  total_area  \
8478          1564812.0            19  13500000.0        77.8   

     first_day_exposition  rooms  ceiling_height  floors_total  

22542            512.0  
      building_series_id  total_images  last_price  total_area  \
23590                NaN             0  21187872.0       123.3   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
23590  2017-04-25T00:00:00      3             NaN           NaN         50.4   

       floor is_apartment  studio   area  open_plan  kitchen_area  balcony  \
23590     18          NaN   False  123.3      False          23.6      0.0   

         locality_name  airports_nearest  cityCenters_nearest  \
23590  Санкт-Петербург           19095.0               4529.0   

       parks_around3000  parks_nearest  ponds_around3000  ponds_nearest  \
23590               0.0            NaN               0.0            NaN   

       days_exposition  
23590            104.0  
      building_series_id  total_images  last_price  total_area  \
20146          1564812.0            16   3850000.0        36.0   

      first_day_exposition  rooms  ceiling_height  floors_t

      building_series_id  total_images  last_price  total_area  \
23658                NaN             6   3063600.0        43.8   

      first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
23658  2016-11-28T00:00:00      1             2.7           NaN         14.0   

       floor is_apartment  studio  area  open_plan  kitchen_area  balcony  \
23658      8          NaN   False  43.8      False          15.5      2.0   

         locality_name  airports_nearest  cityCenters_nearest  \
23658  Санкт-Петербург            8426.0              12082.0   

       parks_around3000  parks_nearest  ponds_around3000  ponds_nearest  \
23658               2.0           24.0               1.0          271.0   

       days_exposition  
23658            246.0  
     building_series_id  total_images  last_price  total_area  \
8478          1564812.0            19  13500000.0        77.8   

     first_day_exposition  rooms  ceiling_height  floors_total  living_area  \
8478  201

KeyboardInterrupt: 

In [ ]:
df_copy.head()

In [ ]:

df_copy = replac(df_copy)
df_copy['floors_total'].isna().sum()

In [ ]:
df_copy['floors_total'].isna().sum()

#### Вывод

С помощью других значений мы можем заполнить часть выборки в данном примере удалось бы по среднему  заполнить 12 значений этажности дома. Но пока мы не будем пользоваться полученными значениями.

### 3.3.2 Приведение типов данных

- first_day_exposition в datetime()
- floors_total / days_exposition - int

In [ ]:
df.info()

In [ ]:
# Заменяем значение на datetime
df['first_day_exposition'] = pd.to_datetime(df['first_day_exposition'], format='%Y-%m-%d')

In [ ]:
# И int где нам нужны целые числа
for column in ['floors_total', 'days_exposition']:
    df[column] = df[column].astype('int')
